# Import Modules

In [1]:
#%matplotlib interactive
%matplotlib widget
#%matplotlib qt

import numpy as np
import math as m
import os as os
import matplotlib.pyplot as plt
import matplotlib.colors as colors
import seaborn
import ipywidgets as widgets
import inspect
import json
from scipy.optimize import curve_fit
from scipy.special import wofz
from matplotlib.pyplot import cm
from IPython.display import display
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from matplotlib.legend_handler import HandlerTuple
from matplotlib.lines import Line2D
from matplotlib.patches import Rectangle
from matplotlib.collections import PatchCollection
from IPython.display import set_matplotlib_formats
set_matplotlib_formats('png', 'pdf')

h = 6.626e-34
me = 9.11e-31
kb = 1.38e-23
cst = np.sqrt(2*me*1.6*10**-19)/(h*10**10)*2*m.pi
fermiLvlTaSe2 = 6.08
fermiLvlTlBiSe = 6


class NumpyEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.ndarray):
            return obj.tolist()
        return json.JSONEncoder.default(self, obj)
#from IPython.core.debugger import set_trace

# Class definition

In [7]:
class arpesData:
    def __init__(self, expFile, expName, cutoff, fermiLvl = fermiLvlTaSe2):
        os.chdir("/mnt/Windows/Users/Flavien/Documents/Mes documents/ENS/MScPolimi/Tesi/Data/TR-ARPES/")
        # path to the data files
        self.expFile = expFile
        self.expName = expName
        
        with open(self.expFile+'/'+self.expName+'.par') as parFile:
            parDict = dict(line.strip('\n').split(':') for line in parFile)
        for key in parDict:
            try:
                setattr(self, key, float(parDict[key]))
            except ValueError:
                setattr(self, key, parDict[key])
        self.delays = np.loadtxt(self.expFile+'/'+self.expName+'.del', dtype=int).tolist()
        if not isinstance(self.delays, list):
            self.delays = [self.delays]
        if abs(min(self.delays))>abs(max(self.delays)):
            self.delays[:] = [-d for d in self.delays]
        self.times = np.array(self.delays)*10/3
        self.nExp = len(self.delays)
        self.size = (260, 250)
        self.cutoff = cutoff
        self.fermiLvl = fermiLvl
        self.E_max = self.E_max - self.fermiLvl
        self.E_min = self.E_min - self.fermiLvl
        
        #r = 5 # range of averaging for the profile
        
        self.E = np.arange(self.E_min, self.E_max, 
                      (self.E_max-self.E_min)/self.size[0])
        self.angles = np.arange(-15, 15, 30/self.size[1])
        self.k = cst*np.sqrt(self.E_max-cutoff)*np.sin(self.angles*m.pi/180)
        self.aa, self.EE = np.meshgrid(self.angles , self.E)
        self.kk = cst*np.sqrt(np.abs(self.EE-cutoff))*np.sin(self.aa*m.pi/180)
        
        self.data = np.zeros((self.size[0], self.size[1], self.nExp))
        for i in range(self.nExp):
            self.data[:, :, i] = np.loadtxt(self.expFile+'/'+self.expName+f'{str(self.delays[i])}.dat')
        #self.data = 1000*self.data/np.max(self.data[:, :, 0])
        
        self.setEDCAtK(0)
        
        
    def setEDCAtK(self, K, r=5):
        step = max(np.diff(self.k))
        profileIndexes = np.stack([(self.kk<K+r*step) & (self.kk>K-r*step)]*self.nExp, axis=-1)
        profileKRange = np.sum(profileIndexes, axis=1)
        profileKRange[profileKRange<0.5] = 1
        self.profiles = np.sum(np.where(profileIndexes, self.data, 0), axis = 1)/profileKRange
        return None

    def setBandFit(self, fitFunc, cutoffFitLower, cutoffFitUpper, onlyAtEq=False):
        self.fitFunc = fitFunc
        self.cutoffFitLower = cutoffFitLower
        self.cutoffFitUpper = cutoffFitUpper
        self.paramFit = np.zeros((self.fitFunc.__code__.co_argcount-1, self.nExp))
        self.paramErrors = np.zeros((self.fitFunc.__code__.co_argcount-1, self.nExp))
        self.profilesFit = np.zeros((np.sum((cutoffFitUpper>self.E)*(self.E>cutoffFitLower)),  self.nExp))
        self.EFit = self.E[(self.cutoffFitUpper>self.E)*(self.E>self.cutoffFitLower)]
        for i in range(self.nExp):
            self.paramFit[:, i], pcov= curve_fit(self.fitFunc, 
                                            self.EFit, 
                                            self.profiles[(cutoffFitUpper>self.E)*(self.E>cutoffFitLower), i],
                                            p0 = list(inspect.getfullargspec(fitFunc)[3]),
                                            bounds = tuple(map(list, zip(*list(fitFunc.__annotations__.values()))))
                                            )
            self.profilesFit[:, i] = self.fitFunc(self.EFit, *self.paramFit[:, i])
            self.paramErrors[:, i] = np.sqrt(np.diag(pcov))
            if onlyAtEq is True:
                break
            #print(paramFit)
        return None
    
    def setBandEdge(self, cutoffEdge = -0.4):
        self.bandEdge = np.zeros(self.nExp)
        self.bandFitEdge = np.zeros(self.nExp)
        for i in range(self.nExp):
            self.bandEdge[i] = self.E[-np.argmax(np.diff(self.profiles[self.E>cutoffEdge, i][::-1], 1))]
            self.bandFitEdge[i] = self.EFit[-np.argmax(np.diff(self.profilesFit[self.EFit>cutoffEdge, i][::-1], 1))]
        return None
    
    def saveParamsToFile(self):
        d = {'times':self.times, 'temperature':self.temperature, 'power':getattr(self, 'pump power'),
             'Name of fit function':self.fitFunc.__name__,
             'Arguments of fit function':str(inspect.getfullargspec(self.fitFunc)),
             'Fit parameters':self.paramFit, 'Fit Errors':self.paramErrors}
        with open('Fit Parameters/' + self.expFile + "_" + self.expName + '.json', 'w') as file:
            json.dump(d, file, cls = NumpyEncoder, indent = 3)
        return None

# Custom fit functions

In [8]:
def gaussian(x, max0:[0,3000] =1800, cen:[5.55,5.85] =5.7, sigma:[0,0.5] =0.07):
    return max0*np.exp(-((x-cen)**2)/((2*sigma)**2))

def voigt(x, gamma, sigma = 5e-2):
    """
    Return the Voigt line shape at x with Gaussian std deviation sigma
    and Lorentzian component HWHM gamma.

    """
    return np.real(wofz((x + 1j*gamma)/sigma/np.sqrt(2)))/(sigma*np.sqrt(2*np.pi))

def voigtMax(area, width):
    return area*voigt(0, width)

def voigtAlt(x, maxPeak, cenPeak, widthL):
    """
    Return the Voigt line shape at x with Gaussian std deviation sigma
    and Lorentzian component HWHM gamma.

    """
    return maxPeak*voigt(x-cenPeak, widthL)/voigt(0, widthL)

def twoLorentzians(x, area1:[0,1500] =100, width1:[0,2] =0.07, cen1:[5,6.5] =5.7,
                   area2:[0,3000] =1500, width2:[0,2] =0.15, cen2:[4.5,6] =5.5):
    return area1/m.pi*width1/((x-cen1)**2+width1**2) + area2/m.pi*width2/((x-cen2)**2+width2**2)

def twoGaussians(x, max1:[60,700] =250, cen1:[-0.365,-0.18] =-0.28, sigma1:[0,0.047] =0.01, 
                 max2:[60,600] =100, cen2:[-0.48,-0.35] =-0.37, sigma2:[0,0.047] =0.01):
    return max1*np.exp(-((x-cen1)**2)/((2*sigma1)**2)) + max2*np.exp(-((x-cen2)**2)/((2*sigma2)**2))

def twoVoigts(x, area1:[0,1000] =350, cen1:[-0.6, -0.3] =-0.4, widthL1:[0,1] =0.05,
             area2:[0,1000] =550, cen2:[-0.7, -0.5] =-0.6, widthL2:[0,1] =0.1): #, widthG:[0,0.5] =0.2):
    """
    widthG corresponds to the resolution of the detector and is the same for both peaks.
    """
    return area1*voigt(x-cen1, widthL1) + area2*voigt(x-cen2, widthL2)

# widthG:[0,0.5] =0.2):
# TaSe2 x, max1:[0,1500] =800, cen1:[-0.6,-0.2] =-0.4, widthL1:[0.005, 0.2] =0.0278, 
# max2:[0,1500] =700, cen2:[-0.7,-0.45] =-0.6):#, widthL2:[0.005, 0.2] =0.08): 
# max1*voigt(x-cen1, widthL1)/voigt(0, widthL1) + max2*voigt(x-cen2,0.095-0.0278+widthL1)/voigt(0, 0.095-0.0278+widthL1) 
def twoVoigtsAlt(x, max1:[0,1500] =800, cen1:[-0.5,-0.3] =-0.4, widthL1:[0, 1] =0.0278, 
                 max2:[0,1500] =700, cen2:[-0.7,-0.5] =-0.6, widthL2:[0, 1] =0.1):                
    """
    widthG corresponds to the resolution of the detector and is the same for both peaks.
    """
    return max1*voigt(x-cen1, widthL1)/voigt(0, widthL1) + max2*voigt(x-cen2, widthL2)/voigt(0, widthL2) 

def fermiDirac(x, u:[5.4, 6.3] =6.1, T:[0.005,1] =0.1):
    return np.max(profiles[:, 0])/(1+np.exp((x-u)/T))

def voigtFermi(x, area1:[0,2000] =800, cen1:[-0.6,-0.2] =-0.4, widthL1:[0,2] =0.2, 
               u:[-0.01, 0.01] =0, T:[0,1] =0.04):
    return area1*voigt(x-cen1, 5e-2, widthL1)/(1+np.exp((x-u)/T))

def lorentzianFermi(x, area1:[0,2000] =800, cen1:[-0.45,-0.32] =-0.4, width1:[0,0.8] =0.2, 
                    u:[-0.001, 0.001] =0, T:[0,2] =0.04):
    return (area1/m.pi)*width1/((x-cen1)**2+width1**2)*1/(1+np.exp((x-u)/T))


# Load data

In [9]:
#cutoff TaSe2 RT = 5.5
#cutoff TaSe2 LT = 5.36 / -0.725
#Bi2Te2Se: fermiLvl=6.08, cutoff = -0.68
#TlBS: fermiLvl=6.08, cutoff = -1.0
#

data = arpesData("20190411", "BTSco", fermiLvl=6.075, cutoff = -0.715)

# Set the reference EDC, band fit and edge

In [10]:
#cutoff Fit TaSe2 LT = 5.49
#cutoff Fit TaSe2 RT = 5.7
# TaSe2 cutoffFitLower = -0.61, cutoffFitUpper = 0)
data.setEDCAtK(0, r=7)

data.setBandFit(twoGaussians, cutoffFitLower = -0.48, cutoffFitUpper = -0.20)
data.setBandEdge(cutoffEdge = -0.38)

## Explore ARPES data with EDCs at various times and k$_\parallel$

In [11]:
try:
    plt.close(fig1)
except NameError:
    print(None)


fig1 = plt.figure(1, (8.5, 6))

axesImg = fig1.add_subplot(121)
img = axesImg.pcolormesh(data.kk, data.EE, data.data[:, :, 0], 
                         shading = 'gouraud', 
                         cmap = 'cubehelix',
                         norm = colors.PowerNorm(gamma=1/2.5))#,
                         #vmin = 4)
edcLine = axesImg.axvline(x = 0, color = 'b', linestyle = ':')
axesImg.set_ylim((data.cutoff, data.E_max))
axesImg.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesImg.set_ylabel('Energy (eV)')
axesImg.set_title(str(data.delays[0]*10/3)+' fs')
fig1.colorbar(img)

E = np.linspace(min(data.E), max(data.E), 2000)

axesGraph = fig1.add_subplot(122, sharey = axesImg)
graphProfiles, = axesGraph.plot(data.profiles[:, 0], data.E, 'k-', lw = 2.5)
graphFit, = axesGraph.plot(data.profilesFit[:, 0], data.E[(data.cutoffFitUpper>data.E)*(data.E>data.cutoffFitLower)], 'C1--')
#bandEdgeLine = axesGraph.axhline(y = bandEdge[0], color = 'r', linestyle = ':')
#bandFitEdgeLine = axesGraph.axhline(y = data.bandFitEdge[0], color = 'k', 
#                                    linestyle = ':', label='Band edge')

graphUpperPeak, = axesGraph.plot(gaussian(E, *data.paramFit[0:3, 0]), E, 'b--')
graphLowerPeak, = axesGraph.plot(gaussian(E, *data.paramFit[3:6, 0]), E, 'r--')

axesGraph.set_xlim((-0.1*np.max(data.profiles), 1.1*np.max(data.profiles)))
#axesGraph.set_ylim((cutoff, float(par['E_max'])))
axesGraph.yaxis.set_ticks_position('right')
axesGraph.yaxis.set_label_position('right')
axesGraph.set_xlabel('ARPES intensity (AU)')
axesGraph.set_ylabel('E-E$_f$ (eV)')
axesGraph.set_title('EDC at k = 0')
axesGraph.grid(True)

def updateDelay(*args):
    img.set_array(np.ravel(data.data[:, :, data.delays.index(delayWidget.value)]))
    graphProfiles.set_xdata(data.profiles[:, data.delays.index(delayWidget.value)])
    graphFit.set_xdata(data.profilesFit[:, data.delays.index(delayWidget.value)])
    graphUpperPeak.set_xdata(gaussian(E, *data.paramFit[0:3, data.delays.index(delayWidget.value)]))
    graphLowerPeak.set_xdata(gaussian(E, *data.paramFit[3:6, data.delays.index(delayWidget.value)]))
    bandFitEdgeLine.set_ydata(data.bandFitEdge[data.delays.index(delayWidget.value)])
    axesImg.set_title(f'{delayWidget.value*10/3} fs')
    plt.draw()
    
def updateEdc(*args):
    edcLine.set_xdata(kEdcWidget.value)
    data.setEDCAtK(kEdcWidget.value, r=8)
    '''profiles[...] = 
    (profilesFit[...], paramFit[...]) = arpesFit(profiles, fitModelUsed)'''
    #data.setBandFit(fitModelUsed, 5.6)
    data.setBandFit(twoGaussians, cutoffFitLower = -0.48, cutoffFitUpper = -0.20)
    graphProfiles.set_xdata(data.profiles[:, data.delays.index(delayWidget.value)])
    graphProfiles.set_ydata(data.E[-np.shape(data.profiles)[0]:])
    graphFit.set_xdata(data.profilesFit[:, data.delays.index(delayWidget.value)])
    graphUpperPeak.set_xdata(gaussian(E, *data.paramFit[0:3, data.delays.index(delayWidget.value)]))
    graphLowerPeak.set_xdata(gaussian(E, *data.paramFit[3:6, data.delays.index(delayWidget.value)]))
    axesGraph.set_title("EDC at k = "+f"{kEdcWidget.value:.2E}")
    plt.draw()
    
delayWidget = widgets.SelectionSlider(
    options = data.delays,
    value = min(data.delays), 
    description = "Delays", 
    continuous_update = False,
    layout = widgets.Layout(width = '80%')
)
delayWidget.observe(updateDelay)

kEdcWidget = widgets.SelectionSlider(
    options = data.k,
    value = data.k[len(data.k)//2],
    #min = min(k)/2.2,
    #max = max(k)/2.2,
    description = "k", 
    continuous_update = False,
    layout = widgets.Layout(width = '90%')
)
kEdcWidget.observe(updateEdc)
display(delayWidget, kEdcWidget)  

#plt.legend()
plt.tight_layout()
plt.show()

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

SelectionSlider(continuous_update=False, description='Delays', layout=Layout(width='80%'), options=(-105, -90,…

SelectionSlider(continuous_update=False, description='k', index=125, layout=Layout(width='90%'), options=(-0.2…

In [ ]:
data.E_max

## Color plot of a EDC at one k over time, with a contour at a given value

In [7]:
try:
    plt.close(fig2)
except NameError:
    print(None)  

fig2 = plt.figure(2, (7, 7))
    
axEDCStack = fig2.add_subplot(311)
TT, ET = np.meshgrid(data.times/1000, data.E)
img2 = axEDCStack.pcolormesh(TT, ET, data.profiles,
             cmap='cubehelix',
             norm=colors.PowerNorm(gamma=1),
             vmin=3
             #vmax=140
             )
'''ax.contour(TT, ET, profiles, #[200:80:-1, :],
          levels = [500], #value of the contour
          colors = 'red'
          #norm = colors.PowerNorm(gamma=1/4),
          #vmin = 0
          )'''

fig2.colorbar(img2)
#ax.set_ylim((cutoff, float(par['E_max'])))
axEDCStack.set_ylim((data.cutoff, 0.5))
#ax.set_xlim((-0.5, 7.5))
#ax.set_zlim(0, 200)
axEDCStack.set_xlabel("Time (ps)")
    

    
axOsc = fig2.add_subplot(312)
#axOsc.plot(data.times, data.bandEdge, 'b-',  label='Band edge')
E = np.linspace(0.2, -0.2, 1000)
bandFitEdge2 = np.zeros(data.nExp)
for i in range(data.nExp):
    bandFitEdge2[i] = E[np.argmax(np.diff(twoVoigtsAlt(E, *data.paramFit[:, i])))]
axOsc.plot(data.times[6:], bandFitEdge2[6:]-bandFitEdge2[0]+0.017*np.exp(-data.times[6:]/500), 'r-+',  label='Band edge from fit')



axparam2= fig2.add_subplot(313)
axparam2.plot(data.times, data.paramFit[2, :], 'b')
axparam2.plot(data.times, data.paramFit[2, :]+0.095-0.0278, 'r')
#axparam2.plot(data.times, data.paramFit[8, :], 'g')
#axparam2.plot(E[:-1], np.diff(lorentzianFermi(E, *data.paramFit[:, 6])), 'b')

plt.tight_layout()
plt.legend

None


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

<ipython-input-7-8bcef94ce427>:12: MatplotlibDeprecationWarning: shading='flat' when X and Y have the same dimensions as C is deprecated since 3.3.  Either specify the corners of the quadrilaterals with X and Y, or pass shading='auto', 'nearest' or 'gouraud', or set rcParams['pcolor.shading'].  This will become an error two minor releases later.
  img2 = axEDCStack.pcolormesh(TT, ET, data.profiles,
<ipython-input-7-8bcef94ce427>:12: MatplotlibDeprecationWarning: Passing parameters norm and vmin/vmax simultaneously is deprecated since 3.3 and will become an error two minor releases later. Please pass vmin/vmax directly to the norm when creating it.
  img2 = axEDCStack.pcolormesh(TT, ET, data.profiles,


<function matplotlib.pyplot.legend(*args, **kwargs)>

# Topological insulators

In [ ]:
dataB1 = arpesData("20190508", "BSTS1", fermiLvl=6.125, cutoff = -0.803)
dataB4 = arpesData("20190508", "BSTS4", fermiLvl=6.037, cutoff = -0.555)

try:
    plt.close(fig9)
except NameError:
    print(None)
    
fig9 = plt.figure(9, figsize = (9.5, 5))

#dataB1.data = 1000*dataB1.data/np.max(dataB1.data[:, :, 0])
#dataB4.data = 1000*dataB4.data/np.max(dataB4.data[:, :, 0])

axesB4 = fig9.add_subplot(131)
imgB4 = axesB4.pcolormesh(dataB4.kk, dataB4.EE, 1000*dataB4.data[:, :, 0]/np.max(dataB4.data[:, :, 0]), 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2),
                             vmin = 8)
axesB4.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesB4.set_xlim((-0.15, 0.15))
axesB4.set_ylim((dataB4.cutoff, 0.75))
axesB4.set_xlabel(r'$k_{//}$ ($\AA^{-1}$)')
axesB4.yaxis.set_ticks_position('right')
axesB4.yaxis.set_label_position('right')
axesB4.tick_params(axis = 'y', which ='major', pad = 10)
axesB4.set_title('(a) Bi$_{2}$Te$_{0.5}$Se$_{2.5}$ at equilibrium')

axesB1 = fig9.add_subplot(132)
imgB1 = axesB1.pcolormesh(dataB1.kk, dataB1.EE, 1000*dataB1.data[:, :, 0]/np.max(dataB1.data[:, :, 0]), 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2),
                             vmin = 8)
axesB1.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesB1.set_ylim((dataB4.cutoff, 0.75))
axesB1.set_xlim((-0.15, 0.15))
axesB1.set_xlabel(r'$k_{//}$ ($\AA^{-1}$)')
axesB1.set_yticklabels(labels = '')
axesB1.set_title('(b) BiSbTeSe$_{2}$ at equilibrium')


axesB1D = fig9.add_subplot(133)
imgB1D = axesB1D.pcolormesh(dataB1.kk, dataB1.EE, 1000*dataB1.data[:, :, 2]/np.max(dataB1.data[:, :, 0]), 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2),
                             vmin = 8)
axesB1D.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesB1D.set_xlim((-0.15, 0.15))
axesB1D.set_ylim((dataB4.cutoff, 0.75))
axesB1D.set_xlabel(r'$k_{//}$ ($\AA^{-1}$)')
axesB1D.set_ylabel('E-E$_f$ (eV)', labelpad = -6)
axesB1D.set_title('(c) BiSbTeSe$_{2}$ at zero\n pump probe delay')

axesCbar = inset_axes(axesB4, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesB4.transAxes,
                      height = '100%', 
                      loc = 'center left')
                      
#fig9.colorbar(imgB1D, cax = axesCbar).set_label(label = 'ARPES intensity (AU)', rotation = 270, labelpad = 15)
fig9.colorbar(imgB4, cax = axesCbar).set_label(label = 'ARPES intensity (AU)', rotation = 90, labelpad = 0)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')

#plt.subplots_adjust(left = 0.02, right = 0.98, bottom = 0.05, top = 0.95)
plt.tight_layout()
plt.subplots_adjust(left = 0.1, wspace = 0.26, right = 0.98)
fig9.savefig('../../Report/Figures/TI-comp.png', dpi = 250)

## Plot of TI populations

In [ ]:
dataPop = arpesData("20190410", "BTS", fermiLvl=6.08, cutoff = -0.68)

try:
    plt.close(fig3)
except NameError:
    print(None)  
    
step = max(np.diff(dataPop.k))

fig3 = plt.figure(3, (9.5, 5.5))
    
boxes = np.array([[-0.003, 83, 0.5, 1.5],
         [-0.005, 33, -0.01, 0.3],
         [0.085, 10, -0.01, 0.07],
         [-0.103, 10, -0.01, 0.07],
         [-0.003, 40, -0.32, -0.18]])
         #[-0.005, 15, -0.16, -0.02]])
         #[-0.066, 12, -0.2, -0.07]])
         

dataPop.setEDCAtK(boxes[0, 0], r=boxes[0, 1])
pop1 = np.sum(dataPop.profiles[(dataPop.E>boxes[0, 2])*(dataPop.E<boxes[0, 3]), :], axis = 0)
pop1 = (pop1-np.min(pop1))/np.max(pop1-np.min(pop1))
pop2 = np.sum(dataPop.profiles[(dataPop.E>boxes[1, 2])*(dataPop.E<boxes[1, 3]), :], axis = 0)
pop2 = (pop2-np.min(pop2))/np.max(pop2-np.min(pop2))

dataPop.setEDCAtK(boxes[2, 0], r=boxes[2, 1])
pop3 = np.sum(dataPop.profiles[(dataPop.E>boxes[2, 2])*(dataPop.E<boxes[2, 3]), :], axis = 0)

dataPop.setEDCAtK(boxes[3, 0], r=boxes[3, 1])
pop3 = pop3 + np.sum(dataPop.profiles[(dataPop.E>boxes[3, 2])*(dataPop.E<boxes[3, 3]), :], axis = 0)
pop3 = (pop3-np.min(pop3))/np.max(pop3-np.min(pop3))

dataPop.setEDCAtK(boxes[4, 0], r=boxes[4, 1])
pop4 = np.sum(dataPop.profiles[(dataPop.E>boxes[4, 2])*(dataPop.E<boxes[4, 3]), :], axis = 0)

#dataPop.setEDCAtK(boxes[5, 0], r=boxes[5, 1])
#pop4 = pop4 + np.sum(dataPop.profiles[(dataPop.E>boxes[5, 2])*(dataPop.E<boxes[5, 3]), :], axis = 0)
pop4 = (pop4-np.min(pop4))/np.max(pop4-np.min(pop4))

#dataPop.setEDCAtK(boxes[5, 0], r=boxes[5, 1])
#pop5 = np.sum(dataPop.profiles[(dataPop.E>boxes[5, 2])*(dataPop.E<boxes[5, 3]), :], axis = 0)
#pop5 = (pop5-np.min(pop5))/np.max(pop5-np.min(pop5))

axesImg = fig3.add_subplot(1, 3, 1)
img = axesImg.pcolormesh(dataPop.kk, dataPop.EE, 1000*dataPop.data[:, :, 10]/np.max(dataPop.data[:, :, 10]), 
                         shading = 'gouraud', 
                         cmap = 'cubehelix',
                         norm = colors.PowerNorm(gamma=1/2.5),
                         vmin = 4)
axesImg.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesImg.set_ylim((dataPop.cutoff, dataPop.E_max))
axesImg.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesImg.set_ylabel('E-E$_f$ (eV)', labelpad=-4)
axesImg.set_title(r'(a) Bi$_{2}$Te$_{2}$Se, '+str(dataPop.delays[10]*10/3)+' fs\n after the pump')
axesImg.yaxis.set_ticks_position('right')
axesImg.yaxis.set_label_position('right')

axesCbar = inset_axes(axesImg, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesImg.transAxes,
                      height = '100%', 
                      loc = 'center left')

fig3.colorbar(img, cax = axesCbar).set_label(label = 'ARPES intensity (AU)', rotation = 90, labelpad = 0)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')

r0 = Rectangle((boxes[0, 0]-boxes[0, 1]*step, boxes[0, 2]), 2*boxes[0, 1]*step, 
               boxes[0, 3]-boxes[0, 2], fill = False, linestyle = '--', color = 'C2', linewidth = 1.5)
r1 = Rectangle((boxes[1, 0]-boxes[1, 1]*step, boxes[1, 2]), 2*boxes[1, 1]*step, 
               boxes[1, 3]-boxes[1, 2], fill = False, linestyle = '--', color = 'C0', linewidth = 1.5)
r21 = Rectangle((boxes[2, 0]-boxes[2, 1]*step, boxes[2, 2]), 2*boxes[2, 1]*step, 
               boxes[2, 3]-boxes[2, 2], fill = False, linestyle = '--', color = 'C1', linewidth = 1.5)
r22 = Rectangle((boxes[3, 0]-boxes[3, 1]*step, boxes[3, 2]), 2*boxes[3, 1]*step, 
               boxes[3, 3]-boxes[3, 2], fill = False, linestyle = '--', color = 'C1', linewidth = 1.5)
r3 = Rectangle((boxes[4, 0]-boxes[4, 1]*step, boxes[4, 2]), 2*boxes[4, 1]*step, 
               boxes[4, 3]-boxes[4, 2], fill = False, linestyle = '--', color = 'C3', linewidth = 1.5)
#r4 = Rectangle((boxes[5, 0]-boxes[5, 1]*step, boxes[5, 2]), 2*boxes[5, 1]*step, 
#               boxes[5, 3]-boxes[5, 2], fill = False, linestyle = '--', color = 'C4', linewidth = 1.5)

axesImg.add_patch(r0)
axesImg.add_patch(r1)
axesImg.add_patch(r21)
axesImg.add_patch(r22)
axesImg.add_patch(r3)
#axesImg.add_patch(r4)

axesPop = fig3.add_subplot(1, 3, (2, 3))
axesPop.plot(dataPop.times, pop1, 'C2s--', label ='High-energy\nconduction band (HCB)')
axesPop.plot(dataPop.times, pop2, 'C0o--', label ='Low-energy\nconduction band (LCB)')
axesPop.plot(dataPop.times, pop3, 'C1v--', label =r'Dirac cone above E$_{f}$ (TSS+)')
axesPop.plot(dataPop.times, pop4, 'C3^--', label =r'Dirac cone below E$_{f}$ (TSS-)')
#axesPop.plot(dataPop.times, pop5, 'C4*--', label ='')
axesPop.set_ylabel('Normalized intensity (AU)')
axesPop.set_xlabel('Time (fs)')
axesPop.yaxis.set_ticks_position('right')
axesPop.yaxis.set_label_position('right')
axesPop.set_title('(b) Electronic dynamics in various regions')
#axesPop.tick_params(tickleft=True)
#axesPop.set_yticklabels(labels = '')
axesPop.grid(True)
axesPop.legend(loc = (0.5, 0.1))

plt.tight_layout()
plt.subplots_adjust(left = 0.095, wspace = 0.47, right = 0.94)
fig3.savefig('../../Report/Figures/TI-dyn.png', dpi = 250)

## Figure Gap opening

In [ ]:
dataB = arpesData("20190410", "BTS", fermiLvl=6.08, cutoff = -0.68)
dataBCL = arpesData("20190410", "BTSCL", fermiLvl=6.08, cutoff = -0.68)
dataBCR = arpesData("20190410", "BTSCR", fermiLvl=6.08, cutoff = -0.68)
dataBpp = arpesData("20190410", "BTSpp", fermiLvl=6.08, cutoff = -0.68)
dataB.data[:, :, 0] = dataB.data[:, :, 0] + dataBCL.data[:, :, 0] + dataBCR.data[:, :, 0] + dataBpp.data[:, :, 0]
#dataB.data[:, :, 0] = dataB.data[:, :, 0] + dataB.data[:, ::-1, 0]
#dataB.data = dataB.data*np.sum(dataB.data, axis=1)[:, None, :]**2


dataBco = arpesData("20190411", "BTSco", fermiLvl=6.075, cutoff = -0.715)
dataBcoCL = arpesData("20190411", "BTScoCL", fermiLvl=6.075, cutoff = -0.715)
dataBcoCR = arpesData("20190411", "BTScoCR", fermiLvl=6.075, cutoff = -0.715)
dataBcopp = arpesData("20190411", "BTScopp", fermiLvl=6.075, cutoff = -0.715)
dataBco.data[:, :, 0] = dataBco.data[:, :, 0] + dataBcoCL.data[:, :, 0] + dataBcoCR.data[:, :, 0] + dataBcopp.data[:, :, 0]
#dataB.data[:, :, 0] = dataB.data[:, :, 0] + dataB.data[:, ::-1, 0]
#dataBco.data = dataBco.data*np.sum(dataBco.data, axis=1)[:, None, :]**2

In [ ]:
#dataB.data = dataB.data*np.sum(dataB.data, axis=1)[:, None, :]
#dataBco.data = dataBco.data*np.sum(dataBco.data, axis=1)[:, None, :]
#dataB.data = (dataB.data)/(np.max(dataB.data, axis=0)[None, :, :]+50)
#dataBco.data = (dataBco.data)/(np.max(dataBco.data, axis=0)[None, :, :]+50)
dataB.data[:, :, 0] = 1000*dataB.data[:, :, 0]/np.max(dataB.data[:, :, 0])
dataBco.data[:, :, 0] = 1000*dataBco.data[:, :, 0]/np.max(dataBco.data[:, :, 0])

In [ ]:
try:
    plt.close(fig10)
except NameError:
    print(None)
    
fig10 = plt.figure(10, figsize = (9.5, 5))

dataB.setEDCAtK(0.0048, r=5)
dataBco.setEDCAtK(0.0069, r=5)

#dataBco.data = 1000*dataBco.data/np.max(dataBco.data[:, :, 0])
#dataB.data = 1000*dataB.data/np.max(dataB.data[:, :, 0])

axesB = fig10.add_subplot(131)
imgB = axesB.pcolormesh(dataB.kk-0.0048, dataB.EE, dataB.data[:, :, 0], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=0.55),
                             vmin = 5)
axesB.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesB.set_ylim((-0.55, 0.2))
axesB.set_xlim((-0.12, 0.12))
axesB.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
#axesB.set_ylabel('E-E$_f$ (eV)', labelpad = -3)
axesB.yaxis.set_ticks_position('right')
axesB.tick_params(axis = 'y', which ='major', pad = 10)
axesB.set_title('(a) Bare Bi$_{2}$Te$_{2}$Se')

axesBco = fig10.add_subplot(132)
imgBco = axesBco.pcolormesh(dataBco.kk-0.0069, dataBco.EE, dataBco.data[:, :, 0], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=0.55),
                             vmin = 5)
axesBco.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesBco.set_ylim((-0.55, 0.2))
axesBco.set_xlim((-0.12, 0.12))
axesBco.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesBco.set_yticklabels(labels = '')
axesBco.set_title('(b) Bi$_{2}$Te$_{2}$Se\nwith deposited cobalt')

axesGraph = fig10.add_subplot(133)
graphProfilesBco, = axesGraph.plot(dataBco.profiles[:, 0], 
                                   dataBco.E, '+--', color = 'r', markersize = 7)
#bandFitEdgeLineBco = axesGraph.axhline(y = dataBco.bandFitEdge[0], color = 'r', 
#                                    linestyle = ':')
graphProfilesB, = axesGraph.plot(dataB.profiles[:, 0], 
                                 dataB.E, '+--', color = 'b', markersize = 7)
#bandFitEdgeLineB = axesGraph.axhline(y = 0, color = 'b', 
#                                    linestyle = ':')
#axesGraph.set_xlim((-15, 1100))
axesGraph.set_ylim((-0.55, 0.2))
axesGraph.set_xlabel('ARPES intensity (AU)', labelpad = 7)
axesGraph.set_ylabel('E-E$_f$ (eV)', labelpad = 3)
#axesGraph.set_xticklabels(labels = '')
#axesGraph.set_xticks(ticks = [])
axesGraph.yaxis.set_ticks_position('left')
axesGraph.yaxis.set_label_position('left')
axesGraph.grid(True)
axesGraph.set_title('(c) EDCs at k=0')
axesGraph.legend([graphProfilesBco, graphProfilesB], 
                 ['Bi$_{2}$Te$_{2}$Se with cobalt', 'Bare Bi$_{2}$Te$_{2}$Se'], 
                 handler_map={tuple: HandlerTuple(None)})

axesCbar = inset_axes(axesB, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesB.transAxes,
                      height = '100%', 
                      loc = 'center left')

                      
fig10.colorbar(imgBco, cax = axesCbar).set_label(label = 'ARPES intensity (AU)', rotation = 90, labelpad = 0)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')

#plt.subplots_adjust(left = 0.02, right = 0.98, bottom = 0.05, top = 0.95)
plt.tight_layout()
plt.subplots_adjust(left = 0.1, wspace = 0.33, right = 0.99)
fig10.savefig('../../Report/Figures/TI-co.png', dpi = 250)

## Waterfall plot of EDCs at various k

In [ ]:
#tIndex = np.abs(times/1000-t).argmin() # closest real value

#dataB = arpesData("20190410", "BTSpp", fermiLvl=6.08, cutoff = -0.68)
def gaussian(x, max0:[40,2000] =600, cen:[-0.36,-0] =-0.28, sigma:[0.03,0.047] =0.04):
    return max0*np.exp(-((x-cen)**2)/((2*sigma)**2))

def twoGaussians1(x, max1:[100,1000] =200, cen1:[-0.36,-0] =-0.28, sigma1:[0.02,0.08] =0.04, 
                 max2:[0,250] =0, cen2:[-0.42,-0.359] =-0.37, sigma2:[0.035,0.05] =0.045):
    return max1*np.exp(-((x-cen1)**2)/((2*sigma1)**2)) + max2*np.exp(-((x-cen2)**2)/((2*sigma2)**2))

def twoGaussians2(x, max1:[20,600] =250, cen1:[-0.365,-0.18] =-0.28, sigma1:[0.02,0.08] =0.04, 
                 max2:[20,600] =100, cen2:[-0.5,-0.4] =-0.45, sigma2:[0.02,0.08] =0.04):
    return max1*np.exp(-((x-cen1)**2)/((2*sigma1)**2)) + max2*np.exp(-((x-cen2)**2)/((2*sigma2)**2))

def twoGaussians3(x, max1:[60,300] =150, cen1:[-0.355,-0.08] =-0.28, sigma1:[0.03,0.05] =0.04, 
                 max2:[60,200] =90, cen2:[-0.38,-0.345] =-0.37, sigma2:[0.03,0.05] =0.04):
    return max1*np.exp(-((x-cen1)**2)/((2*sigma1)**2)) + max2*np.exp(-((x-cen2)**2)/((2*sigma2)**2))

def twoGaussians4(x, max1:[70,1000] =250, cen1:[-0.36,-0.08] =-0.28, sigma1:[0.02,0.08] =0.04, 
                 max2:[30,1000] =100, cen2:[-0.51,-0.365] =-0.45, sigma2:[0.03,0.08] =0.04):
    return max1*np.exp(-((x-cen1)**2)/((2*sigma1)**2)) + max2*np.exp(-((x-cen2)**2)/((2*sigma2)**2))
try:
    plt.close(fig11)
except NameError:
    print(None)
    
fig11 = plt.figure(11, (9.5, 7.5))
    
axesWB = fig11.add_subplot(221)
axesWBco = fig11.add_subplot(222)
axesDisp = fig11.add_subplot(2,2,(3,4))
nCurves = 30 # Number of curves
nPoints = 10

kWCurves = np.linspace(-0.055, 0.0, nCurves)
indexPoints = np.arange(nCurves)[2::3]
kWPoints = kWCurves[indexPoints] #np.linspace(-0.055, 0.0, nPoints)
bandPos = np.zeros(len(kWPoints))
bandPosErros = np.zeros(len(kWPoints))
bandcoPos = np.zeros(len(kWPoints))
bandcoPosErros = np.zeros(len(kWPoints))
edcPad = 0.15
j=0

for i in range(nCurves):
    dataB.setEDCAtK(kWCurves[i]+0.0048, r=3)
    axesWB.plot(dataB.profiles[:, 0]/np.max(dataB.profiles[:, 0]) + edcPad*i, dataB.E, 'k')
    dataBco.setEDCAtK(kWCurves[i]+0.0069, r=3)
    axesWBco.plot(dataBco.profiles[:, 0]/np.max(dataBco.profiles[:, 0]) + edcPad*i, dataBco.E, 'k')
    if i in indexPoints:
        dataB.setBandFit(gaussian, cutoffFitLower = -0.37, cutoffFitUpper = -0.11, onlyAtEq = True)
        axesWB.plot(1 + edcPad*i, dataB.paramFit[1, 0], 'd', color = 'b')

        dataBco.setBandFit(gaussian, cutoffFitLower = -0.35, cutoffFitUpper = -0.11, onlyAtEq = True)
        axesWBco.plot(1 + edcPad*i, dataBco.paramFit[1, 0], 'v', color = 'r')       
        
        '''if j==0:
            axesDisp.errorbar(kWPoints[j], dataB.paramFit[1, 0], yerr = 2*dataB.paramErrors[1, 0], 
                              fmt = 'd', color = 'b', capsize = 2, 
                              label = 'Position of the band maxima for bare Bi$_{2}$Te$_{2}$Se')
            axesDisp.errorbar(kWPoints[j], dataBco.paramFit[1, 0], yerr = 2*dataBco.paramErrors[1, 0], 
                              fmt = 'v', color = 'r', capsize = 2, 
                              label = 'Position of the band maxima for Bi$_{2}$Te$_{2}$Se with cobalt')'''
       
        axesDisp.errorbar(kWPoints[j], dataB.paramFit[1, 0], yerr = 2*dataB.paramErrors[1, 0], 
                          fmt = 'd', color = 'b', capsize = 2)
        axesDisp.errorbar(kWPoints[j], dataBco.paramFit[1, 0], yerr = 2*dataBco.paramErrors[1, 0], 
                          fmt = 'v', color = 'r', capsize = 2)
        bandPos[j] = dataB.paramFit[1, 0]
        bandPosErros[j] = dataB.paramErrors[1, 0]
        bandcoPos[j] = dataBco.paramFit[1, 0]
        bandcoPosErros[j] = dataB.paramErrors[1, 0]
        j = j+1
    
hamTop = lambda x, a, b: a*np.abs(x) + b
bandPosFit, pcov= curve_fit(hamTop,
                    kWPoints, 
                    bandPos,
                    p0 = [4, -0.363],
                    sigma = bandPosErros            
                    )

hamTopco = lambda x, a, b: ((a*x)**2 + b**2)**0.5 + bandPosFit[1]
bandcoPosFit, pcov= curve_fit(hamTopco,
                    kWPoints, 
                    bandcoPos,
                    p0 = [4, 0.1],
                    sigma = bandcoPosErros            
                    )

a = Line2D([], [], marker='d', color='b', linewidth=0, label='Position of the band maxima for bare Bi$_{2}$Te$_{2}$Se')
b = Line2D([], [], marker='v', color='r', linewidth=0, label='Position of the band maxima for Bi$_{2}$Te$_{2}$Se with cobalt')
c, = axesDisp.plot(kWPoints, hamTop(kWPoints, *bandPosFit), 'b--', label='Linear dispersion relation fit') 
d, = axesDisp.plot(kWPoints, hamTopco(kWPoints, *bandcoPosFit), 'r--', label='Massive dispersion relation fit')
axesDisp.legend(loc=3, handles=[a, c, b, d])
axesDisp.grid(True)
axesDisp.set_ylim(-0.39, -0.16)
axesDisp.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesDisp.set_ylabel('E-E$_{f}$ (eV)')
axesDisp.set_title('(c) Comparison of the edge states dispersion relation')


axesWB.set_ylim(-0.42, -0.1)
axesWB.set_ylabel('E-E$_{f}$ (eV)', labelpad=7)
axesWB.yaxis.set_ticks_position('right')
axesWB.yaxis.set_label_position('right')
axesWB.set_xticks([0.3, 4.8])
axesWB.set_xticklabels(labels = ['$k_{//} = -0.55$ $\AA^{-1}$', '$k_{//} = 0$ $\AA^{-1}$'])
axesWB.tick_params(axis='x', which=u'both',  length=0)
axesWB.set_title('(a) Normalized EDCs for bare Bi$_{2}$Te$_{2}$Se')

axesWBco.set_ylim(-0.42, -0.1)
axesWBco.set_yticklabels(labels = '')
axesWBco.set_xticks([0.3, 4.9])
axesWBco.set_xticklabels(labels = ['$k_{//} = -0.55$ $\AA^{-1}$', '$k_{//} = 0$ $\AA^{-1}$'])
axesWBco.tick_params(axis='x', which=u'both',  length=0)
axesWBco.set_title('(b) Normalized EDCs for Bi$_{2}$Te$_{2}$Se\nwith deposited cobalt')


plt.tight_layout()
plt.subplots_adjust(left = 0.085, wspace = 0.25, right = 0.99, bottom = 0.07, top = 0.94)
fig11.savefig('../../Report/Figures/TI-EDCs-gap.png', dpi = 250)

In [ ]:
bandPosFit

# Charge density wave compound : 1T-TaSe$_2$

In [ ]:
3.405*2*m.pi*1e-10*1.6e-19/(h)

In [ ]:
0.0634*1.61e-19/(516613)**2/me

In [ ]:
dataRT = arpesData("20190208", "TaSe3p2", -0.58)
dataLT = arpesData("20190214", "TaSeLT1p6", -0.725)

fitModelUsedRT = lorentzianFermi
dataRT.setBandFit(fitModelUsedRT, cutoffFitLower = -0.36, cutoffFitUpper = 0.5)
dataRT.setBandEdge(cutoffEdge = -0.2)

fitModelUsedLT = twoVoigts
dataLT.setBandFit(fitModelUsedLT, cutoffFitLower = -0.6, cutoffFitUpper = 0.5)
dataLT.setBandEdge(cutoffEdge = -0.4)

## Figure comparison low and high temperature

In [ ]:
try:
    plt.close(fig5)
except NameError:
    print(None)
    
fig5 = plt.figure(5, figsize = (9.5, 5))

dataRT.data = 1000*dataRT.data/np.max(dataRT.data[:, :, 0])
dataLT.data = 1000*dataLT.data/np.max(dataLT.data[:, :, 0])
dataRT.setEDCAtK(0)
dataLT.setEDCAtK(0)


axesImgRT = fig5.add_subplot(132)
imgRT = axesImgRT.pcolormesh(dataRT.kk, dataRT.EE, dataRT.data[:, :, 0], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2),
                             vmin = 5)
axesImgRT.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesImgRT.set_xlim((-0.15, 0.15))
axesImgRT.set_ylim((dataRT.cutoff, 0.7))
axesImgRT.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesImgRT.set_title('(b) 1T-TaSe$_{2}$ at room\ntemperature')
axesImgRT.set_yticklabels(labels = '')

axesImgLT = fig5.add_subplot(131)
imgLT = axesImgLT.pcolormesh(dataLT.kk, dataLT.EE, dataLT.data[:, :, 0], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2),
                             vmin = 5)
axesImgLT.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesImgLT.set_xlim((-0.15, 0.15))
axesImgLT.set_ylim((dataRT.cutoff, 0.7))
axesImgLT.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
axesImgLT.yaxis.set_ticks_position('right')
axesImgLT.yaxis.set_label_position('right')
axesImgLT.tick_params(axis = 'y', which ='major', pad = 10)
axesImgLT.set_title('(a) 1T-TaSe$_{2}$ at low\ntemperature (80K)')


axesGraph = fig5.add_subplot(133)
graphProfilesLT, = axesGraph.plot(dataLT.profiles[:, 0], dataLT.E, 'r+--')
bandFitEdgeLineLT = axesGraph.axhline(y = dataLT.bandFitEdge[0], color = 'r', 
                                    linestyle = ':')
graphProfilesRT, = axesGraph.plot(dataRT.profiles[:, 0], dataRT.E, 'b+--')
bandFitEdgeLineRT = axesGraph.axhline(y = 0, color = 'b', 
                                    linestyle = ':')
axesGraph.set_xlim((-0.1*np.max(dataLT.profiles), 1.1*np.max(dataLT.profiles)))
axesGraph.set_ylim((dataRT.cutoff, 0.7))
#axesGraph.yaxis.set_ticks_position('right')
#axesGraph.yaxis.set_label_position('right')
axesGraph.set_xlabel('ARPES intensity (AU)')
axesGraph.set_ylabel('E-E$_{f}$ (eV)', labelpad=-3)
axesGraph.set_title('(c) EDCs at k = 0')
axesGraph.grid(True)
axesGraph.legend([graphProfilesRT, graphProfilesLT, (bandFitEdgeLineLT, bandFitEdgeLineRT)], 
                 ['Room\ntemperature', 'Low\ntemperature (80K)', 'Band Edges'], 
                 handler_map={tuple: HandlerTuple(None)})
axesGraph.annotate('', xy = (210, dataLT.bandFitEdge[0]), 
                   xytext = (210, dataRT.bandFitEdge[0]),
                   arrowprops=dict(facecolor='black', shrinkA = 1, shrinkB = 1,
                                   lw= 1, arrowstyle = "<->"))
axesGraph.text(250, (dataLT.bandFitEdge[0])/2-0.03, 
               f'Gap opening\nof 300 meV',# {m.floor(1000*(-dataLT.bandFitEdge[0]))} meV', 
               fontsize = 7)

axesCbar = inset_axes(axesImgLT, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesImgLT.transAxes,
                      height = '100%', 
                      loc = 'center left')
                      
fig5.colorbar(imgRT, cax = axesCbar).set_label(label = 'ARPES intensity (AU)', rotation = 90, labelpad = 0)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')

plt.tight_layout()
plt.subplots_adjust(left = 0.096, right = 0.99, bottom = 0.095, top = 0.91, wspace = 0.27)
fig5.savefig('../../Report/Figures/CDW-temp-comp.png', dpi = 250)

In [ ]:
dataRT = arpesData("20190208", "TaSe3p2", -0.58)
dataRT.data = 1000*dataRT.data/np.max(dataRT.data[:, :, 0])

## Figure evolution room temperature

In [ ]:
from matplotlib.pyplot import cm

try:
    plt.close(fig6)
except NameError:
    print(None)

a=7.8
b=0.23
def lorentzianFermi2(x, area1:[0,5000] =800, cen1:[-0.45,-0.28] =-0.36, #width1:[0,0.8] =0.2, 
                    u:[-0.001, 0.001] =0, T:[0,2] =0.04):
    return (area1/m.pi)*(a*T+b)/((x-cen1)**2+(a*T+b)**2)*1/(1+np.exp((x-u)/T))

dataRT.setEDCAtK(0, r=10)
#dataRT.profiles=1000*dataRT.profiles/np.max(dataRT.profiles[:, 0])
dataRT.setBandFit(lorentzianFermi2, cutoffFitLower = -0.4, cutoffFitUpper = 0.5)
dataRT.setBandEdge(-0.2)
    
fig6 = plt.figure(6, figsize = (9.5, 10.5))


axesImgRT = fig6.add_subplot(4, 3, (1, 4))
imgRT = axesImgRT.pcolormesh(dataRT.kk, dataRT.EE, dataRT.data[:, :, 0], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2.5),
                             vmin = 8)
axesImgRT.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesImgRT.set_xlim((-0.15, 0.15))
axesImgRT.set_ylim((dataRT.cutoff,0.7))
axesImgRT.yaxis.set_ticks_position('right')
axesImgRT.tick_params(axis = 'y', which ='major', pad = 10)
#axesImgRT.yaxis.set_label_position('right')
axesImgRT.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
#axesImgRT.set_ylabel('E-E_f (eV)')
axesImgRT.set_title('(a) Signal at equilibrium')

axesCbar = inset_axes(axesImgRT, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesImgRT.transAxes,
                      height = '100%', 
                      loc = 'center left')                    
cbar = fig6.colorbar(imgRT, cax = axesCbar)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')
cbar.set_label(label = 'ARPES intensity (AU)')

axesImgRT2 = fig6.add_subplot(4, 3, (2, 5))
imgRT2 = axesImgRT2.pcolormesh(dataRT.kk, dataRT.EE, dataRT.data[:, :, 7], 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/2.5),
                             vmin = 8)
axesImgRT2.axhline(y = 0, color = 'w', linestyle = '--', linewidth = 0.75)
axesImgRT2.set_xlim((-0.15, 0.15))
axesImgRT2.set_ylim((dataRT.cutoff, 0.7))
axesImgRT2.set_xlabel('$k_{//}$ ($\AA^{-1}$)')
#axesImgRT2.yaxis.set_label_position('right')
axesImgRT2.set_yticklabels(labels = '')
#axesImgRT2.set_ylabel('E-E$_f$ (eV)')
axesImgRT2.set_title('(b) Signal '+str(dataRT.delays[7]*10/3)+' fs\n after the pump')

axesGraph = fig6.add_subplot(4, 3, (3, 6), sharey = axesImgRT)
axesGraph.plot(dataRT.profiles[:, 0], dataRT.E, 'k', label = f'{dataRT.times[0]} fs', lw = 2.5)
color = cm.brg(np.linspace(0,1,6))
for i, c in zip([6,7,10,12,19,22], color):
    axesGraph.plot(dataRT.profiles[:, i], dataRT.E, label = f'{dataRT.times[i]} fs', c=c, lw = 0.9)  
axesGraph.set_xlim((-0.1*np.max(dataRT.profiles), 1.1*np.max(dataRT.profiles)))
axesGraph.set_xlabel('ARPES intensity (AU)')
axesGraph.set_ylabel('E-E$_f$ (eV)', labelpad = -4)
axesGraph.set_title('(c) EDCs at k = 0\nover time')
axesGraph.grid(True)
axesGraph.legend()


axesTemp = fig6.add_subplot(4, 3, (7, 9))                            
temperature = (1.6e-19/kb)*(dataRT.paramFit[3, :]**2-(0.08/4)**2)**0.5
axesTemp.plot(dataRT.times/1000, temperature, 'k+', label = 'Electronic temperature from F-D distribution')
axesTemp.fill_between(dataRT.times/1000, temperature-2*(1.6e-19/kb)*dataRT.paramErrors[3, :],
                         temperature+2*(1.6e-19/kb)*dataRT.paramErrors[3, :], 
                         alpha = 0.18, facecolor = 'k', edgecolor = None)
tempDecay = lambda x, T0, A, t : T0 + A*np.exp(-x/t)
tempDecayFit, pcov= curve_fit(tempDecay,
                        dataRT.times[7:], 
                        temperature[7:],
                        sigma = (1.6e-19/kb)*dataRT.paramErrors[3, 7:],
                        p0 = [25, 40, 300])                          
axesTemp.plot(dataRT.times[8:]/1000, tempDecay(dataRT.times[8:], *tempDecayFit), 'C1--', linewidth=2,
              label = f'Exponential fit of temperature\nDecay time ~{tempDecayFit[2]:.2E} fs')
axesTemp.set_xlabel('Time (ps)')
axesTemp.set_ylabel('Temperature (K)')
axesTemp.set_yticks([300, 500, 700, 900])
axesTemp.set_title('(d) Evolution of the electronic temperature')
axesTemp.grid(True)
axesTemp.legend()

axesBandPos = fig6.add_subplot(4, 3, (10, 12))
axesBandPos.plot(dataRT.times/1000, dataRT.paramFit[1, :]-dataRT.paramFit[1, 0], 'k+',
                 label = 'Position of the band')
axesBandPos.fill_between(dataRT.times/1000, dataRT.paramFit[1, :]-dataRT.paramFit[1, 0]-2*dataRT.paramErrors[1, :],
                         dataRT.paramFit[1, :]-dataRT.paramFit[1, 0]+2*dataRT.paramErrors[1, :], 
                         alpha = 0.18, facecolor = 'k', edgecolor = None)
bandPos = lambda x, P0, A, B, f, phi: P0 + A*np.exp(-x/tempDecayFit[2]) + B*np.sin(2*m.pi*f*x+phi)
bandPosFit, pcov= curve_fit(bandPos,
                        dataRT.times[14:-7], 
                        dataRT.paramFit[1, 14:-7]-dataRT.paramFit[1, 0],
                        sigma = dataRT.paramErrors[1, 14:-7],
                        p0 = [0, -1, 0.5, 1/500, 0])
axesBandPos.plot(dataRT.times[14:-7]/1000, bandPos(dataRT.times[14:-7], *bandPosFit), 'C1--', linewidth=2, 
                 label = f'Fit of the oscillations\nFrequency ~{1e15*bandPosFit[3]:.2E} Hz')
axesBandPos.set_xlabel('Time (ps)')
axesBandPos.set_ylabel('Binding energy (eV)')
axesBandPos.set_title('(e) Shift of the band relative to its equilibrium position')
axesBandPos.grid(True)
axesBandPos.legend(loc=4)

plt.tight_layout()
plt.subplots_adjust(left = 0.105, right = 0.99, bottom = 0.045, top = 0.955, wspace = 0.27, hspace=0.6)
fig6.savefig('../../Report/Figures/CDW-RT', dpi = 250)

In [ ]:
bandPosFit

In [ ]:
np.sqrt(np.diag(pcov))

In [ ]:
dataLT = arpesData("20190214", "TaSeLT8p8", -0.725)
dataLT.data = 1000*dataLT.data/np.max(dataLT.data[:, :, 0])
dataLT.setEDCAtK(0, r=10)

dataLT.setBandFit(twoVoigtsAlt, cutoffFitLower = -0.61, cutoffFitUpper = 0.5)
dataLT.setBandEdge(cutoffEdge = -0.38)

## Figure evolution low temperature

In [ ]:
try:
    plt.close(fig7)
except NameError:
    print(None)
    
fig7 = plt.figure(7, figsize = (9.5, 9.5))


axesImgLT = fig7.add_subplot(4, 2, (1, 3))
imgRT = axesImgLT.pcolormesh(dataLT.times/1000, dataLT.E, dataLT.profiles, 
                             shading = 'gouraud', 
                             cmap = 'cubehelix',
                             norm = colors.PowerNorm(gamma=1/1.5),
                             vmin = 8)
axesImgLT.set_ylim((dataLT.cutoff,0.4))
axesImgLT.yaxis.set_ticks_position('right')
axesImgLT.yaxis.set_label_position('right')
axesImgLT.set_xlabel('Time (ps)')
#axesImgLT.set_ylabel('E-E_f (eV)')
axesImgLT.set_ylabel('E-E$_f$ (eV)', labelpad = 7)
axesImgLT.set_title('(a) ARPES signal at $k=0$')

axesCbar = inset_axes(axesImgLT, width = '6%', 
                      bbox_to_anchor = (-0.15, 0., 1, 1), 
                      bbox_transform = axesImgLT.transAxes,
                      height = '100%', 
                      loc = 'center left')                    
cbar = fig7.colorbar(imgRT, cax = axesCbar)
axesCbar.yaxis.set_ticks_position('left')
axesCbar.yaxis.set_label_position('left')
cbar.set_label(label = 'ARPES intensity (AU)')


axesGraph = fig7.add_subplot(4, 2, (2, 4))
axesGraph.plot(dataLT.profiles[:, 0], dataLT.E, 'k', label = f'{dataLT.times[0]} fs', lw = 2.5)
color = cm.brg(np.linspace(0,1,7))
# [6,7,10,15,17,22,25,36,45] 8.8mW
for i, c in zip([3,4,5,6,10,18,27], color):
    axesGraph.plot(dataLT.profiles[:, i], dataLT.E, label = f'{dataLT.times[i]} fs', c=c, lw = 0.9)  
axesGraph.set_xlim((-0.1*np.max(dataLT.profiles), 1.1*np.max(dataLT.profiles)))
axesGraph.set_ylim((dataLT.cutoff,0.4))
axesGraph.set_xlabel('ARPES intensity (AU)')
axesGraph.set_yticklabels(labels = '')
axesGraph.set_title('(b) EDCs at $k=0$ over time')

axesGraph.grid(True)
axesGraph.legend()


axesBandPos = fig7.add_subplot(4, 2, (5, 6))                            
                      
axesBandPos.plot(dataLT.times/1000, dataLT.paramFit[1, :]-dataLT.paramFit[1, 0], 'b+', label='Upper band')
axesBandPos.fill_between(dataLT.times/1000, dataLT.paramFit[1, :]-dataLT.paramFit[1, 0]-2*dataLT.paramErrors[1, :],
                         dataLT.paramFit[1, :]-dataLT.paramFit[1, 0]+2*dataLT.paramErrors[1, :], 
                         alpha = 0.25, facecolor = 'b', edgecolor = None)
axesBandPos.plot(dataLT.times/1000, dataLT.paramFit[4, :]-dataLT.paramFit[4, 0], 'r+', label='Lower band')
axesBandPos.fill_between(dataLT.times/1000, dataLT.paramFit[4, :]-dataLT.paramFit[4, 0]-2*dataLT.paramErrors[4, :],
                         dataLT.paramFit[4, :]-dataLT.paramFit[4, 0]+2*dataLT.paramErrors[4, :], 
                         alpha = 0.25, facecolor = 'r', edgecolor = None)
#axesBandPos.plot(dataLT.times/1000, dataLT.paramFit[4, :]-dataLT.paramFit[4, 0]-(dataLT.paramFit[1, :]-dataLT.paramFit[1, 0]),
#                 'g-', label='Difference')
axesBandPos.set_xlabel('Time (ps)')
axesBandPos.set_ylabel('Energy (eV)')
#axesBandPos.set_yticks([300, 500, 700, 900])abs
axesBandPos.set_title('(c) Shift of the bands relative to their equilibrium position')
#axesBandPos.set_xlim((-1, 9))
axesBandPos.grid(True)
axesBandPos.legend()

axesDepl = fig7.add_subplot(4, 2, (7, 8))
axesDepl.plot(dataLT.times/1000, dataLT.paramFit[0, :]/dataLT.paramFit[0, 0], 'b+', label='Upper band')
axesDepl.fill_between(dataLT.times/1000, dataLT.paramFit[0, :]/dataLT.paramFit[0, 0]-2*dataLT.paramErrors[0, :]/dataLT.paramFit[0, :],
                         dataLT.paramFit[0, :]/dataLT.paramFit[0, 0]+2*dataLT.paramErrors[0, :]/dataLT.paramFit[0, :], 
                         alpha = 0.25, facecolor = 'b', edgecolor = None)
axesDepl.plot(dataLT.times/1000, dataLT.paramFit[3, :]/dataLT.paramFit[3, 0], 'r+', label='Lower band')
axesDepl.fill_between(dataLT.times/1000, dataLT.paramFit[3, :]/dataLT.paramFit[3, 0]-2*dataLT.paramErrors[3, :]/dataLT.paramFit[3, :],
                         dataLT.paramFit[3, :]/dataLT.paramFit[3, 0]+2*dataLT.paramErrors[3, :]/dataLT.paramFit[3, :],
                         alpha = 0.25, facecolor = 'r', edgecolor = None)
axesDepl.set_title('(d) Depletion of the bands')
axesDepl.set_xlabel('Time (ps)')
axesDepl.set_ylabel('Normalized intensity')
axesDepl.grid(True)
axesDepl.legend()

axesGraph.text(470, dataLT.paramFit[1, 0]-0.025, 
               f'Upper band', color = 'b',
               fontsize = 7)

axesGraph.text(380, dataLT.paramFit[4, 0]-0.01, 
               f'Lower band', color = 'r',
               fontsize = 7)

plt.tight_layout()
plt.subplots_adjust(left = 0.115, right = 0.99, bottom = 0.05, top = 0.97, wspace = 0.23, hspace=0.6)
fig7.savefig('../../Report/Figures/CDW-LT', dpi = 250)

In [ ]:
#dataLT.saveParamsToFile()

In [ ]:
try:
    plt.close(fig8)
except NameError:
    print(None)
    

    
fig8 = plt.figure(8, figsize = (9, 9.5))

axes = fig8.subplots(4, 2, sharex = True).ravel()
n = len(axes)
i = 0
color = cm.brg(np.linspace(0,1,4))
paramIndexes = [1,4,0,3,2]
for fileName in os.listdir('Fit Parameters/'):
    if fileName.endswith('.json'):
        with open('Fit Parameters/' + fileName, 'r') as file:
            json_load = json.load(file)
        if type(json_load['temperature']) is float:
            times = np.asarray(json_load['times'])/1000
            paramFit = np.asarray(json_load['Fit parameters'])
            errorFit = np.asarray(json_load['Fit Errors'])
            errorFit[0, :] = errorFit[0, :]/paramFit[0, :]
            errorFit[3, :] = errorFit[3, :]/paramFit[3, :]
            paramFit[1, :] = paramFit[1, :]-paramFit[1, 0]
            paramFit[4, :] = paramFit[4, :]-paramFit[4, 0]
            paramFit[0, :] = paramFit[0, :]/paramFit[0, 0]
            paramFit[3, :] = paramFit[3, :]/paramFit[3, 0]
            
            if json_load['power']>9:
                    break
            
            for j in range(len(paramIndexes)):
                
                if json_load['power']>9:
                    times = times -0.09
                axes[j].plot(times, paramFit[paramIndexes[j], :], '+-', c=color[i], label = str(json_load['power']))
                axes[j].fill_between(times, paramFit[paramIndexes[j], :]-2*errorFit[paramIndexes[j], :],
                                     paramFit[paramIndexes[j], :]+2*errorFit[paramIndexes[j], :],
                                     alpha = 0.5, facecolor = color[i], edgecolor = None)
                
                if json_load['power']>9:
                    break

            axes[5].plot(times, paramFit[2, :]+0.095-0.0278, '+-', c=color[i], label = str(json_load['power']))
            axes[5].fill_between(times, paramFit[2, :]+0.095-0.0278-2*errorFit[paramIndexes[j], :],
                                 paramFit[2, :]+0.095-0.0278+2*errorFit[paramIndexes[j], :],
                                 alpha = 0.5, facecolor = color[i], edgecolor = None)
            
            axes[6].plot(times, paramFit[0, :]/voigt(0, paramFit[2, :])/(paramFit[0, 0]/voigt(0, paramFit[2, 0])), '+-', c=color[i], label = str(json_load['power']))
            axes[7].plot(times, paramFit[3, :]/voigt(0, paramFit[2, :]+0.095-0.0278)/(paramFit[0, 0]/voigt(0, paramFit[2, 0]+0.095-0.0278)), '+-', c=color[i], label = str(json_load['power']))
            i = i+1
            
axes[0].set_xlim(-0.5, 5)
axes[0].legend()
'''axes[:].set_title(['Band shift of the upper band', 'Band shift of the lower band', 'Depletion of the upper band',
                   'Depletion of the lower band', 'Width of the upper band', 'Width of the lower band', 
                   'Shift of the difference between the bands', ''])'''

axes[0].set_title('Band shift of the upper band')
axes[0].set_xlabel('Time (ps)')
axes[0].grid(True)

axes[1].set_title('Band shift of the lower band')
axes[1].set_xlabel('Time (ps)')
axes[1].set_ylabel('Energy (eV)')
axes[1].grid(True)

axes[2].set_title('Depletion of the upper band')
axes[2].grid(True)

axes[3].set_title('Depletion of the lower band')
axes[3].grid(True)

axes[4].set_title('Width of the upper band')
axes[4].grid(True)

axes[5].set_title('Width of the lower band')
axes[5].grid(True)

axes[6].set_title('Area of the upper band')
axes[6].grid(True)

axes[7].set_title('Area of the lower band')
axes[7].grid(True)

plt.tight_layout()

## Figure summary of oscillations for all fluences

In [ ]:
import matplotlib.collections as mcol

try:
    plt.close(fig9)
except NameError:
    print(None)

    
fig9 = plt.figure(9, figsize = (9.5, 7.5))
axesOscillation = fig9.add_subplot(2, 3, (1,3), title = '(a) Relative upper band shift for various pump powers',
                                  xlabel = 'Time (fs)', ylabel = 'Shift in energy (eV)')
axesFrequency = fig9.add_subplot(2, 3, 4, title = '(b) Frequency of oscillations', 
                                 xlabel = 'Power of the pump (mW)', 
                                 ylabel = 'Frequency (x10$^{12}$ Hz)')
axesAmpl = fig9.add_subplot(2, 3, 5, sharex = axesFrequency, title = '(c) Amplitude of oscillations', 
                            xlabel = 'Power of the pump (mW)',
                            ylabel = 'Amplitude (meV)')
axesPhase = fig9.add_subplot(2, 3, 6, sharex = axesFrequency, title = '(d) Phase of oscillations', 
                             xlabel = 'Power of the pump (mW)',
                             ylabel = 'Degrees °')

#axesDecay = fig9.add_subplot(2,3, 6, title = 'Times constant of the exponential decay', xlabel = 'Power of the pump (mW)')

oscillation = lambda x, P0, B, f, phi: P0 + B*np.sin(2*m.pi*f*x+phi*m.pi/180) #+ A*np.exp(-x/T0)
timesFine = np.linspace(1000, 2000, 1000)

#amplitude = lambda x, a, b, c: a

i = 0
color = cm.brg([0,0.25,0.5,0.9])

for fileName in os.listdir('Fit Parameters/'):
    if fileName.endswith('.json'):
        with open('Fit Parameters/' + fileName, 'r') as file:
            json_load = json.load(file)
        if json_load['power']>9:
                break
        if type(json_load['temperature']) is float:
            times = np.asarray(json_load['times'])/1000
            paramFit = np.asarray(json_load['Fit parameters'])
            errorFit = np.asarray(json_load['Fit Errors'])
            paramFit[1, :] = paramFit[1, :]-paramFit[1, 0]
            paramFit[4, :] = paramFit[4, :]-paramFit[4, 0]
            
            axesOscillation.plot(times*1000, paramFit[1, :], '+', c=color[i], label = str(json_load['power'])+' mW')
            axesOscillation.fill_between(times*1000, paramFit[1, :]-2*errorFit[1, :],
                                 paramFit[1, :]+2*errorFit[1, :],
                                 alpha = 0.25, facecolor = color[i], edgecolor = None)
            bandPosFit, pcov= curve_fit(oscillation,
                        times[(times>=1)*(times<=2)]*1000, 
                        paramFit[1, (times>=1)*(times<=2)],
                        p0 = [0, 0.01, 1/500, 0],
                        bounds = ([-0.5, 0, 0, -180,], [0.5, 1, 0.01, 180])               
                        )
            bandPosErr = np.sqrt(np.diag(pcov))
            axesOscillation.plot(timesFine, oscillation(timesFine, *bandPosFit), '--',
                                 c=color[i], lw=2)
            
            axesFrequency.errorbar(json_load['power'], bandPosFit[2]*1e3, yerr = 2*bandPosErr[2]*1e3, 
                                   fmt = 's', c=color[i], capsize = 2)
            axesPhase.errorbar(json_load['power'], bandPosFit[3],
                               yerr = 2*bandPosErr[3], fmt = 's', c=color[i], capsize = 2)
            axesAmpl.errorbar(json_load['power'], 2*1000*bandPosFit[1], yerr = 2*2000*bandPosErr[1], 
                                   fmt = 's', c=color[i], capsize = 2)
            axesAmpl.plot(np.linspace(0,10,100), 21*np.linspace(0,10,100)/8.1, 'k--')
            i = i+1

line = [[(0, 0)]]
lc = mcol.LineCollection(4* line, linestyles='--', colors=color)
axesOscillation.set_xlim(-300, 2000)
axesOscillation.grid(True)
axesOscillation.legend(loc=2)
#axesOscillation.legend(lc, 
#                 ['Fits'], 
#                 handler_map={tuple: HandlerTuple(None)})
axesFrequency.set_ylim(2.2, 2.45)
axesFrequency.grid(True)
axesAmpl.set_xlim(0, 10)
axesAmpl.set_ylim(0, 28)
axesAmpl.grid(True)
axesPhase.grid(True)

plt.tight_layout()
plt.subplots_adjust(left = 0.08, right = 0.98, bottom = 0.06, top = 0.97, wspace = 0.35, hspace=0.4)
fig9.savefig('../../Report/Figures/CDW-osc', dpi = 250)